In [1]:
from datetime import datetime

from binance.client import Client
from binance.enums import *

from coinmarketcapapi import CoinMarketCapAPI, CoinMarketCapAPIError

from datetime import datetime
from binance.helpers import round_step_size

import numpy as np
import pandas as pd
import json
import time
import sys


In [2]:
#client = Client('', '')

In [3]:
#cmc = CoinMarketCapAPI('')

In [4]:
#info = client.get_all_tickers()

In [5]:
#quote_ccy = 'USDT'

In [6]:
#ticker_list = [d['symbol'] for d in info if d['symbol'].endswith(quote_ccy)]

In [7]:
#rank_info = cmc.cryptocurrency_map(sort='cmc_rank').data

In [8]:
#target_rank_info = [d['symbol']+quote_ccy for d in rank_info if d['rank'] >= 100 and d['rank'] <= 500]

In [9]:
#target_ticker_list = [d for d in ticker_list if d in target_rank_info]

In [10]:
#target_ticker_list

In [11]:
#target_ticker_list = ['BONDUSDT']

In [12]:
global client;

In [13]:
global target_ticker_list

In [14]:
def init():
    global client
    client = Client('', '', {"verify": True, "timeout": 20})
    cmc = CoinMarketCapAPI('')
    info_all_tickers  = client.get_all_tickers()
    quote_ccy = 'USDT'
    ticker_list = [d['symbol'] for d in info_all_tickers if d['symbol'].endswith(quote_ccy)]
    rank_info = cmc.cryptocurrency_map(sort='cmc_rank').data
    target_rank_info = [d['symbol']+quote_ccy for d in rank_info if d['rank'] >= 1 and d['rank'] <= 50]
    global target_ticker_list
    rank_filtered_ticker_list = [d for d in ticker_list if d in target_rank_info]
    # target_ticker_list = ['RIFUSDT']
    pair_details = client.get_all_isolated_margin_symbols()
    margin_pair_list = [d['symbol'] for d in pair_details if d['quote'] == quote_ccy and d['isMarginTrade'] == True]   
    target_ticker_list = [d for d in rank_filtered_ticker_list if d in margin_pair_list]
    #target_ticker_list = ['BTCUSDT']
    #target_ticker_list = rank_filtered_ticker_list 
    return target_ticker_list
    

In [15]:
def is_candidate(filtered_klines_info): 
    is_candidate = False
    
    buy_kline_info = filtered_klines_info[0]
    buy_kline_average_volume = buy_kline_info[5]

    
    strong_context_kline_info = filtered_klines_info[1:len(filtered_klines_info)]


    
    strong_context_kline_average_volume = np.mean(strong_context_kline_info[:,5])
    
    for strong_context_kline in strong_context_kline_info:
        perc_change = strong_context_kline[-1]
        perc_volume = strong_context_kline[5] / buy_kline_average_volume


        if perc_change > 1 or perc_change < -2.0 or perc_volume > 0.55:
            return False
    

    buy_line_open_price = buy_kline_info[1]
    buy_line_high_price = buy_kline_info[2]
    buy_line_low_price = buy_kline_info[3]
    buy_line_close_price = buy_kline_info[4]

    #Drop from high price to close price should be in the range of 10 - 15%
    drop_from_high_to_close_gate =   1.20 > buy_line_high_price/buy_line_close_price > 1.05


    #Percentage increase should be in the range of 7 - 15%
    percentage_gate = -2 > buy_kline_info[-1] > -5

    if percentage_gate and True and True:

        is_candidate = True
    else:
        is_candidate = False

    return is_candidate

In [16]:
def find_percentage_increase_or_decrease(focused_kline_array):
    percentage_value = []
    for kline in focused_kline_array:
        diff = kline[4] - kline[1]
        perc_diff = diff/kline[1]
        percentage_value.append(perc_diff*100)
    return percentage_value 

In [17]:
trade_list = []
init()
test_run = False
print('Total Tickers to Analyze')
print(len(target_ticker_list))
count = 1
for target_ticker in target_ticker_list:
    
    print('Analyzing Hourly Started ')
    print(target_ticker)
    print(count)
    count = count + 1

    klines = client.get_historical_klines(target_ticker, Client.KLINE_INTERVAL_1HOUR, "1440 day ago UTC") 
    

    
    
    
    length = int(len(klines))
    if(length < 24):
        continue
    

    #klines.pop()
    
    

    

    array = np.array(klines, dtype=np.float64)
    focused_kline_array = np.delete(array, [6, 7, 8, 9, 10, 11], 1)
    percentage_value = find_percentage_increase_or_decrease(focused_kline_array)
    # reduce lengrth below if poped
    percentage_value = np.reshape(percentage_value, (length, 1))
    focused_kline_array = np.append(focused_kline_array, percentage_value, 1)
    
    focused_reverse_kline_array = focused_kline_array[::-1]

    for x in range(0, length):

        hit_ticker_dictionary = {}
        
        filtered_klines_info = focused_reverse_kline_array[x:x+5]


        if(len(filtered_klines_info) == 5):


            
            if(is_candidate(filtered_klines_info)):
                    
                
                    
                buy_kline_info = filtered_klines_info[0]
                hit_ticker_dictionary = {}
                buy_price = buy_kline_info[4]
                hit_ticker_dictionary['ticker'] = target_ticker
                hit_ticker_dictionary['buy_price'] = buy_kline_info[4]

                buy_timesstamp = buy_kline_info[0]
                hit_ticker_dictionary['buy_datetime'] = str(datetime.fromtimestamp(buy_timesstamp // 1000))
                
                proft_percentage = 1.35
                loss_percentage = 0.8
                profit_sell_price = buy_price * proft_percentage
                loss_sell_price = buy_price * loss_percentage
                
                
                
                usdt = 1000
                
                buy_quantity = usdt/buy_price
                hit_ticker_dictionary['quantity'] = buy_quantity
                
                
 
                
                for y in range(0, x) :
                    
                    start = x - (y + 1)
                    end = x - y
                    
                    high_price = focused_reverse_kline_array[start:end][0][2]
                    low_price = focused_reverse_kline_array[start:end][0][3]
                    close_price = focused_reverse_kline_array[start:end][0][4]
                    sell_timesstamp = focused_reverse_kline_array[start:end][0][0]
                    sell_datetime = str(datetime.fromtimestamp(sell_timesstamp // 1000))
                    
                    if high_price >= profit_sell_price:
                        hit_ticker_dictionary['sell_price'] = profit_sell_price

                        hit_ticker_dictionary['sell_datetime'] = str(datetime.fromtimestamp(sell_timesstamp // 1000))
                        difference = focused_reverse_kline_array[start:end][0][0] - buy_kline_info[0]
                        
                        hit_ticker_dictionary['days_to_gain_loss'] = round(difference/(1000 * 60 * 24 * 60))
                        price_difference = profit_sell_price - buy_price
                        hit_ticker_dictionary['price_diff'] = price_difference
                        hit_ticker_dictionary['proft_loss'] = usdt * proft_percentage - usdt
                        break
                    elif sell_timesstamp - buy_timesstamp >= 6600000 :
                        hit_ticker_dictionary['sell_price'] = close_price

                        hit_ticker_dictionary['sell_datetime'] = str(datetime.fromtimestamp(sell_timesstamp // 1000))
                        difference = focused_reverse_kline_array[start:end][0][0] - buy_kline_info[0]
                        
                        hit_ticker_dictionary['days_to_gain_loss'] = round(difference/(1000 * 60 * 24 * 60))
                        price_difference = close_price - buy_price
                        hit_ticker_dictionary['price_diff'] = price_difference
                        hit_ticker_dictionary['proft_loss'] = buy_quantity * close_price - buy_quantity * buy_price
                        break   
                    elif False: # low_price <=  loss_sell_price:
                        hit_ticker_dictionary['sell_price'] = loss_sell_price

                        hit_ticker_dictionary['sell_datetime'] = str(datetime.fromtimestamp(sell_timesstamp // 1000))
                        difference = focused_reverse_kline_array[start:end][0][0] - buy_kline_info[0]
                        
                        hit_ticker_dictionary['days_to_gain_loss'] = round(difference/(1000 * 60 * 24 * 60))
                        price_difference = loss_sell_price - buy_price
                        hit_ticker_dictionary['price_diff'] = price_difference
                        hit_ticker_dictionary['proft_loss'] = usdt * loss_percentage - usdt
                        break
                        
                        
                trade_list.append(hit_ticker_dictionary)        


Total Tickers to Analyze
43
Analyzing Hourly Started 
BTCUSDT
1


/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:16: RuntimeWarning: divide by zero encountered in double_scalars
  app.launch_new_instance()


Analyzing Hourly Started 
ETHUSDT
2
Analyzing Hourly Started 
BNBUSDT
3
Analyzing Hourly Started 
LTCUSDT
4
Analyzing Hourly Started 
ADAUSDT
5
Analyzing Hourly Started 
XRPUSDT
6
Analyzing Hourly Started 
EOSUSDT
7
Analyzing Hourly Started 
TUSDUSDT
8
Analyzing Hourly Started 
XLMUSDT
9
Analyzing Hourly Started 
TRXUSDT
10
Analyzing Hourly Started 
ETCUSDT
11


/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:16: RuntimeWarning: invalid value encountered in double_scalars
  app.launch_new_instance()


Analyzing Hourly Started 
VETUSDT
12
Analyzing Hourly Started 
USDCUSDT
13
Analyzing Hourly Started 
LINKUSDT
14
Analyzing Hourly Started 
XMRUSDT
15
Analyzing Hourly Started 
ZECUSDT
16
Analyzing Hourly Started 
THETAUSDT
17
Analyzing Hourly Started 
MATICUSDT
18
Analyzing Hourly Started 
ATOMUSDT
19
Analyzing Hourly Started 
ALGOUSDT
20
Analyzing Hourly Started 
DOGEUSDT
21
Analyzing Hourly Started 
BUSDUSDT
22
Analyzing Hourly Started 
XTZUSDT
23
Analyzing Hourly Started 
HBARUSDT
24
Analyzing Hourly Started 
BCHUSDT
25
Analyzing Hourly Started 
FTTUSDT
26
Analyzing Hourly Started 
SOLUSDT
27
Analyzing Hourly Started 
MANAUSDT
28
Analyzing Hourly Started 
SANDUSDT
29
Analyzing Hourly Started 
DOTUSDT
30
Analyzing Hourly Started 
EGLDUSDT
31
Analyzing Hourly Started 
UNIUSDT
32
Analyzing Hourly Started 
AVAXUSDT
33
Analyzing Hourly Started 
HNTUSDT
34
Analyzing Hourly Started 
AAVEUSDT
35
Analyzing Hourly Started 
NEARUSDT
36
Analyzing Hourly Started 
FILUSDT
37
Analyzing Hourly Star

In [18]:
trade_list

[{'ticker': 'BTCUSDT',
  'buy_price': 19165.01,
  'buy_datetime': '2022-07-13 14:00:00',
  'quantity': 0.05217842307413354,
  'sell_price': 19574.57,
  'sell_datetime': '2022-07-13 16:00:00',
  'days_to_gain_loss': 0,
  'price_diff': 409.5600000000013,
  'proft_loss': 21.37019495424215},
 {'ticker': 'BTCUSDT',
  'buy_price': 19420.34,
  'buy_datetime': '2022-06-30 08:00:00',
  'quantity': 0.05149240435543353,
  'sell_price': 19234.06,
  'sell_datetime': '2022-06-30 10:00:00',
  'days_to_gain_loss': 0,
  'price_diff': -186.27999999999884,
  'proft_loss': -9.59200508333015},
 {'ticker': 'BTCUSDT',
  'buy_price': 20737.81,
  'buy_datetime': '2022-06-27 15:00:00',
  'quantity': 0.04822109952786721,
  'sell_price': 20754.73,
  'sell_datetime': '2022-06-27 17:00:00',
  'days_to_gain_loss': 0,
  'price_diff': 16.919999999998254,
  'proft_loss': 0.8159010040113799},
 {'ticker': 'BTCUSDT',
  'buy_price': 19439.26,
  'buy_datetime': '2022-06-18 08:00:00',
  'quantity': 0.05144228741217516,
  'se

In [19]:
a = 10
b = 5

step = -1 if a > b else 1
for x in range (a, b, step):
    print(x, end = ' ')

10 9 8 7 6 

In [20]:
len(trade_list)

4346

In [21]:
df = pd.DataFrame.from_dict(trade_list)

In [22]:
print('Profit and Loss')
df['proft_loss'].sum()

Profit and Loss


5442.285898512306

In [23]:
print('Number of Profit Trades')
df[df['price_diff'] > 0].shape[0]

Number of Profit Trades


2456

In [24]:
print('Number of Loss Trades')
df[df['price_diff'] < 0].shape[0]

Number of Loss Trades


1847

In [25]:
with pd.option_context('display.max_rows', None):
    display(df[np.invert(pd.isna(df['sell_price']))].sort_values('buy_datetime'))

ticker     buy_price         buy_datetime      quantity  \
1434    TRXUSDT      0.024650  2018-09-03 06:00:00  4.056795e+04   
133     BTCUSDT   7092.110000  2018-09-05 11:00:00  1.410018e-01   
611     LTCUSDT     64.660000  2018-09-05 11:00:00  1.546551e+01   
411     BNBUSDT     10.892700  2018-09-05 11:00:00  9.180460e+01   
132     BTCUSDT   6700.000000  2018-09-06 01:00:00  1.492537e-01   
774     ADAUSDT      0.082610  2018-09-07 12:00:00  1.210507e+04   
131     BTCUSDT   6212.330000  2018-09-08 19:00:00  1.609702e-01   
610     LTCUSDT     53.010000  2018-09-08 19:00:00  1.886437e+01   
1608    ETCUSDT     11.010500  2018-09-08 19:00:00  9.082240e+01   
1433    TRXUSDT      0.019410  2018-09-08 19:00:00  5.151984e+04   
1142    EOSUSDT      4.796500  2018-09-08 19:00:00  2.084854e+02   
1758    VETUSDT      0.014770  2018-09-08 19:00:00  6.770481e+04   
934     XRPUSDT      0.276680  2018-09-08 19:00:00  3.614284e+03   
773     ADAUSDT      0.078690  2018-09-08 19:00:00  1.270810e+04   
410     BNBUSDT      9.620300  2018-09-08 19:00:00  1.039469e+02   
772     ADAUSDT      0.074480  2018-09-09 04:00:00  1.342642e+04   
1757    VETUSDT      0.014380  2018-09-10 00:00:00  6.954103e+04   
933     XRPUSDT      0.261420  2018-09-10 18:00:00  3.825262e+03   
1607    ETCUSDT     10.516300  2018-09-12 05:00:00  9.509048e+01   
1292    XLMUSDT      0.199980  2018-09-14 10:00:00  5.000500e+03   
1756    VETUSDT      0.013520  2018-09-14 10:00:00  7.396450e+04   
1432    TRXUSDT      0.019190  2018-09-17 16:00:00  5.211047e+04   
1141    EOSUSDT      5.136800  2018-09-17 16:00:00  1.946737e+02   
771     ADAUSDT      0.066300  2018-09-17 16:00:00  1.508296e+04   
1755    VETUSDT      0.013220  2018-09-17 16:00:00  7.564297e+04   
770     ADAUSDT      0.062920  2018-09-17 22:00:00  1.589320e+04   
130     BTCUSDT   6167.400000  2018-09-19 20:00:00  1.621429e-01   
1754    VETUSDT      0.012510  2018-09-19 20:00:00  7.993605e+04   
1753    VETUSDT      0.013520  2018-09-22 10:00:00  7.396450e+04   
299     ETHUSDT    235.500000  2018-09-22 10:00:00  4.246285e+00   
609     LTCUSDT     58.280000  2018-09-22 10:00:00  1.715854e+01   
409     BNBUSDT     10.072500  2018-09-22 10:00:00  9.928022e+01   
298     ETHUSDT    234.370000  2018-09-24 08:00:00  4.266758e+00   
1752    VETUSDT      0.013280  2018-09-24 08:00:00  7.530120e+04   
769     ADAUSDT      0.086060  2018-09-24 08:00:00  1.161980e+04   
297     ETHUSDT    228.610000  2018-09-25 00:00:00  4.374262e+00   
1140    EOSUSDT      5.494100  2018-09-25 02:00:00  1.820134e+02   
1139    EOSUSDT      5.163500  2018-09-25 08:00:00  1.936671e+02   
1138    EOSUSDT      5.529100  2018-09-30 22:00:00  1.808613e+02   
932     XRPUSDT      0.516920  2018-10-03 01:00:00  1.934535e+03   
768     ADAUSDT      0.079870  2018-10-03 04:00:00  1.252035e+04   
608     LTCUSDT     57.470000  2018-10-06 13:00:00  1.740038e+01   
931     XRPUSDT      0.493750  2018-10-06 15:00:00  2.025316e+03   
607     LTCUSDT     56.890000  2018-10-11 02:00:00  1.757778e+01   
296     ETHUSDT    220.810000  2018-10-11 02:00:00  4.528780e+00   
767     ADAUSDT      0.083000  2018-10-11 02:00:00  1.204819e+04   
129     BTCUSDT   6367.820000  2018-10-11 03:00:00  1.570396e-01   
408     BNBUSDT     10.043600  2018-10-11 03:00:00  9.956589e+01   
1606    ETCUSDT     10.330900  2018-10-11 03:00:00  9.679699e+01   
606     LTCUSDT     51.360000  2018-10-12 01:00:00  1.947040e+01   
1137    EOSUSDT      5.096500  2018-10-12 01:00:00  1.962131e+02   
295     ETHUSDT    191.580000  2018-10-12 01:00:00  5.219752e+00   
766     ADAUSDT      0.070790  2018-10-12 01:00:00  1.412629e+04   
765     ADAUSDT      0.071700  2018-10-15 01:00:00  1.394700e+04   
930     XRPUSDT      0.409940  2018-10-15 01:00:00  2.439381e+03   
929     XRPUSDT      0.460050  2018-10-18 19:00:00  2.173677e+03   
764     ADAUSDT      0.074450  2018-10-23 12:00:00  1.343183e+04   
1605    ETCUSDT      9.400800  2018-10-29 12:00:00  1.063739e+02 

In [26]:
with pd.option_context('display.max_rows', None):
    display(df.sort_values('buy_datetime'))

ticker     buy_price         buy_datetime      quantity  \
1434    TRXUSDT      0.024650  2018-09-03 06:00:00  4.056795e+04   
133     BTCUSDT   7092.110000  2018-09-05 11:00:00  1.410018e-01   
611     LTCUSDT     64.660000  2018-09-05 11:00:00  1.546551e+01   
411     BNBUSDT     10.892700  2018-09-05 11:00:00  9.180460e+01   
132     BTCUSDT   6700.000000  2018-09-06 01:00:00  1.492537e-01   
774     ADAUSDT      0.082610  2018-09-07 12:00:00  1.210507e+04   
131     BTCUSDT   6212.330000  2018-09-08 19:00:00  1.609702e-01   
610     LTCUSDT     53.010000  2018-09-08 19:00:00  1.886437e+01   
1608    ETCUSDT     11.010500  2018-09-08 19:00:00  9.082240e+01   
1433    TRXUSDT      0.019410  2018-09-08 19:00:00  5.151984e+04   
1142    EOSUSDT      4.796500  2018-09-08 19:00:00  2.084854e+02   
1758    VETUSDT      0.014770  2018-09-08 19:00:00  6.770481e+04   
934     XRPUSDT      0.276680  2018-09-08 19:00:00  3.614284e+03   
773     ADAUSDT      0.078690  2018-09-08 19:00:00  1.270810e+04   
410     BNBUSDT      9.620300  2018-09-08 19:00:00  1.039469e+02   
772     ADAUSDT      0.074480  2018-09-09 04:00:00  1.342642e+04   
1757    VETUSDT      0.014380  2018-09-10 00:00:00  6.954103e+04   
933     XRPUSDT      0.261420  2018-09-10 18:00:00  3.825262e+03   
1607    ETCUSDT     10.516300  2018-09-12 05:00:00  9.509048e+01   
1292    XLMUSDT      0.199980  2018-09-14 10:00:00  5.000500e+03   
1756    VETUSDT      0.013520  2018-09-14 10:00:00  7.396450e+04   
1432    TRXUSDT      0.019190  2018-09-17 16:00:00  5.211047e+04   
1141    EOSUSDT      5.136800  2018-09-17 16:00:00  1.946737e+02   
771     ADAUSDT      0.066300  2018-09-17 16:00:00  1.508296e+04   
1755    VETUSDT      0.013220  2018-09-17 16:00:00  7.564297e+04   
770     ADAUSDT      0.062920  2018-09-17 22:00:00  1.589320e+04   
130     BTCUSDT   6167.400000  2018-09-19 20:00:00  1.621429e-01   
1754    VETUSDT      0.012510  2018-09-19 20:00:00  7.993605e+04   
1753    VETUSDT      0.013520  2018-09-22 10:00:00  7.396450e+04   
299     ETHUSDT    235.500000  2018-09-22 10:00:00  4.246285e+00   
609     LTCUSDT     58.280000  2018-09-22 10:00:00  1.715854e+01   
409     BNBUSDT     10.072500  2018-09-22 10:00:00  9.928022e+01   
298     ETHUSDT    234.370000  2018-09-24 08:00:00  4.266758e+00   
1752    VETUSDT      0.013280  2018-09-24 08:00:00  7.530120e+04   
769     ADAUSDT      0.086060  2018-09-24 08:00:00  1.161980e+04   
297     ETHUSDT    228.610000  2018-09-25 00:00:00  4.374262e+00   
1140    EOSUSDT      5.494100  2018-09-25 02:00:00  1.820134e+02   
1139    EOSUSDT      5.163500  2018-09-25 08:00:00  1.936671e+02   
1138    EOSUSDT      5.529100  2018-09-30 22:00:00  1.808613e+02   
932     XRPUSDT      0.516920  2018-10-03 01:00:00  1.934535e+03   
768     ADAUSDT      0.079870  2018-10-03 04:00:00  1.252035e+04   
608     LTCUSDT     57.470000  2018-10-06 13:00:00  1.740038e+01   
931     XRPUSDT      0.493750  2018-10-06 15:00:00  2.025316e+03   
607     LTCUSDT     56.890000  2018-10-11 02:00:00  1.757778e+01   
296     ETHUSDT    220.810000  2018-10-11 02:00:00  4.528780e+00   
767     ADAUSDT      0.083000  2018-10-11 02:00:00  1.204819e+04   
129     BTCUSDT   6367.820000  2018-10-11 03:00:00  1.570396e-01   
408     BNBUSDT     10.043600  2018-10-11 03:00:00  9.956589e+01   
1606    ETCUSDT     10.330900  2018-10-11 03:00:00  9.679699e+01   
606     LTCUSDT     51.360000  2018-10-12 01:00:00  1.947040e+01   
1137    EOSUSDT      5.096500  2018-10-12 01:00:00  1.962131e+02   
295     ETHUSDT    191.580000  2018-10-12 01:00:00  5.219752e+00   
766     ADAUSDT      0.070790  2018-10-12 01:00:00  1.412629e+04   
765     ADAUSDT      0.071700  2018-10-15 01:00:00  1.394700e+04   
930     XRPUSDT      0.409940  2018-10-15 01:00:00  2.439381e+03   
929     XRPUSDT      0.460050  2018-10-18 19:00:00  2.173677e+03   
764     ADAUSDT      0.074450  2018-10-23 12:00:00  1.343183e+04   
1605    ETCUSDT      9.400800  2018-10-29 12:00:00  1.063739e+02 

In [27]:
with pd.option_context('display.max_rows', None):
    display(df[df['price_diff'] > 0].sort_values('buy_datetime'))

ticker     buy_price         buy_datetime      quantity  \
1434    TRXUSDT      0.024650  2018-09-03 06:00:00  4.056795e+04   
774     ADAUSDT      0.082610  2018-09-07 12:00:00  1.210507e+04   
772     ADAUSDT      0.074480  2018-09-09 04:00:00  1.342642e+04   
1757    VETUSDT      0.014380  2018-09-10 00:00:00  6.954103e+04   
933     XRPUSDT      0.261420  2018-09-10 18:00:00  3.825262e+03   
1607    ETCUSDT     10.516300  2018-09-12 05:00:00  9.509048e+01   
1756    VETUSDT      0.013520  2018-09-14 10:00:00  7.396450e+04   
1292    XLMUSDT      0.199980  2018-09-14 10:00:00  5.000500e+03   
770     ADAUSDT      0.062920  2018-09-17 22:00:00  1.589320e+04   
130     BTCUSDT   6167.400000  2018-09-19 20:00:00  1.621429e-01   
1754    VETUSDT      0.012510  2018-09-19 20:00:00  7.993605e+04   
1753    VETUSDT      0.013520  2018-09-22 10:00:00  7.396450e+04   
609     LTCUSDT     58.280000  2018-09-22 10:00:00  1.715854e+01   
299     ETHUSDT    235.500000  2018-09-22 10:00:00  4.246285e+00   
409     BNBUSDT     10.072500  2018-09-22 10:00:00  9.928022e+01   
1139    EOSUSDT      5.163500  2018-09-25 08:00:00  1.936671e+02   
1138    EOSUSDT      5.529100  2018-09-30 22:00:00  1.808613e+02   
932     XRPUSDT      0.516920  2018-10-03 01:00:00  1.934535e+03   
1137    EOSUSDT      5.096500  2018-10-12 01:00:00  1.962131e+02   
606     LTCUSDT     51.360000  2018-10-12 01:00:00  1.947040e+01   
766     ADAUSDT      0.070790  2018-10-12 01:00:00  1.412629e+04   
295     ETHUSDT    191.580000  2018-10-12 01:00:00  5.219752e+00   
765     ADAUSDT      0.071700  2018-10-15 01:00:00  1.394700e+04   
930     XRPUSDT      0.409940  2018-10-15 01:00:00  2.439381e+03   
929     XRPUSDT      0.460050  2018-10-18 19:00:00  2.173677e+03   
764     ADAUSDT      0.074450  2018-10-23 12:00:00  1.343183e+04   
605     LTCUSDT     48.920000  2018-10-29 13:00:00  2.044154e+01   
294     ETHUSDT    197.550000  2018-10-29 13:00:00  5.062010e+00   
1431    TRXUSDT      0.022110  2018-10-29 13:00:00  4.522840e+04   
928     XRPUSDT      0.441800  2018-10-29 13:00:00  2.263468e+03   
1751    VETUSDT      0.010150  2018-10-30 19:00:00  9.852217e+04   
604     LTCUSDT     53.370000  2018-11-05 02:00:00  1.873712e+01   
603     LTCUSDT     50.360000  2018-11-11 16:00:00  1.985703e+01   
1604    ETCUSDT      9.128200  2018-11-11 16:00:00  1.095506e+02   
1291    XLMUSDT      0.260340  2018-11-13 19:00:00  3.841131e+03   
926     XRPUSDT      0.473810  2018-11-14 16:00:00  2.110551e+03   
405     BNBUSDT      5.495700  2018-11-24 08:00:00  1.819604e+02   
404     BNBUSDT      5.076300  2018-11-24 22:00:00  1.969939e+02   
923     XRPUSDT      0.359630  2018-11-30 11:00:00  2.780636e+03   
124     BTCUSDT   4005.000000  2018-12-03 03:00:00  2.496879e-01   
290     ETHUSDT    113.430000  2018-12-03 03:00:00  8.816010e+00   
1429    TRXUSDT      0.014220  2018-12-03 03:00:00  7.032349e+04   
598     LTCUSDT     32.300000  2018-12-03 03:00:00  3.095975e+01   
922     XRPUSDT      0.360340  2018-12-03 03:00:00  2.775157e+03   
1289    XLMUSDT      0.155880  2018-12-03 03:00:00  6.415191e+03   
760     ADAUSDT      0.040050  2018-12-03 03:00:00  2.496879e+04   
289     ETHUSDT    108.000000  2018-12-03 16:00:00  9.259259e+00   
1747    VETUSDT      0.004540  2018-12-03 16:00:00  2.202643e+05   
123     BTCUSDT   3882.860000  2018-12-03 16:00:00  2.575421e-01   
597     LTCUSDT     30.600000  2018-12-03 16:00:00  3.267974e+01   
759     ADAUSDT      0.038390  2018-12-03 16:00:00  2.604845e+04   
122     BTCUSDT   3765.010000  2018-12-05 17:00:00  2.656035e-01   
288     ETHUSDT    103.600000  2018-12-05 17:00:00  9.652510e+00   
1287    XLMUSDT      0.139600  2018-12-05 17:00:00  7.163324e+03   
403     BNBUSDT      4.643100  2018-12-10 07:00:00  2.153733e+02   
1601    ETCUSDT      3.776000  2018-12-10 07:00:00  2.648305e+02   
595     LTCUSDT     23.070000  2018-12-13 21:00:00  4.334634e+01   
1131    EOSUSDT      1.801700  2018-12-15 10:00:00  5.550314e+02 

In [28]:
with pd.option_context('display.max_rows', None):
    display(df[df['price_diff'] < 0].sort_values('buy_datetime'))

ticker     buy_price         buy_datetime      quantity  \
133     BTCUSDT   7092.110000  2018-09-05 11:00:00  1.410018e-01   
411     BNBUSDT     10.892700  2018-09-05 11:00:00  9.180460e+01   
611     LTCUSDT     64.660000  2018-09-05 11:00:00  1.546551e+01   
132     BTCUSDT   6700.000000  2018-09-06 01:00:00  1.492537e-01   
131     BTCUSDT   6212.330000  2018-09-08 19:00:00  1.609702e-01   
610     LTCUSDT     53.010000  2018-09-08 19:00:00  1.886437e+01   
1433    TRXUSDT      0.019410  2018-09-08 19:00:00  5.151984e+04   
1142    EOSUSDT      4.796500  2018-09-08 19:00:00  2.084854e+02   
1608    ETCUSDT     11.010500  2018-09-08 19:00:00  9.082240e+01   
1758    VETUSDT      0.014770  2018-09-08 19:00:00  6.770481e+04   
934     XRPUSDT      0.276680  2018-09-08 19:00:00  3.614284e+03   
410     BNBUSDT      9.620300  2018-09-08 19:00:00  1.039469e+02   
773     ADAUSDT      0.078690  2018-09-08 19:00:00  1.270810e+04   
1432    TRXUSDT      0.019190  2018-09-17 16:00:00  5.211047e+04   
1141    EOSUSDT      5.136800  2018-09-17 16:00:00  1.946737e+02   
1755    VETUSDT      0.013220  2018-09-17 16:00:00  7.564297e+04   
771     ADAUSDT      0.066300  2018-09-17 16:00:00  1.508296e+04   
769     ADAUSDT      0.086060  2018-09-24 08:00:00  1.161980e+04   
298     ETHUSDT    234.370000  2018-09-24 08:00:00  4.266758e+00   
1752    VETUSDT      0.013280  2018-09-24 08:00:00  7.530120e+04   
297     ETHUSDT    228.610000  2018-09-25 00:00:00  4.374262e+00   
1140    EOSUSDT      5.494100  2018-09-25 02:00:00  1.820134e+02   
608     LTCUSDT     57.470000  2018-10-06 13:00:00  1.740038e+01   
931     XRPUSDT      0.493750  2018-10-06 15:00:00  2.025316e+03   
767     ADAUSDT      0.083000  2018-10-11 02:00:00  1.204819e+04   
296     ETHUSDT    220.810000  2018-10-11 02:00:00  4.528780e+00   
607     LTCUSDT     56.890000  2018-10-11 02:00:00  1.757778e+01   
129     BTCUSDT   6367.820000  2018-10-11 03:00:00  1.570396e-01   
408     BNBUSDT     10.043600  2018-10-11 03:00:00  9.956589e+01   
1606    ETCUSDT     10.330900  2018-10-11 03:00:00  9.679699e+01   
1605    ETCUSDT      9.400800  2018-10-29 12:00:00  1.063739e+02   
927     XRPUSDT      0.526350  2018-11-08 03:00:00  1.899877e+03   
763     ADAUSDT      0.072570  2018-11-14 10:00:00  1.377980e+04   
1136    EOSUSDT      4.877300  2018-11-14 16:00:00  2.050315e+02   
407     BNBUSDT      8.966800  2018-11-14 16:00:00  1.115225e+02   
293     ETHUSDT    191.490000  2018-11-14 16:00:00  5.222205e+00   
602     LTCUSDT     47.690000  2018-11-14 16:00:00  2.096876e+01   
128     BTCUSDT   5965.110000  2018-11-14 17:00:00  1.676415e-01   
127     BTCUSDT   5590.000000  2018-11-15 11:00:00  1.788909e-01   
1750    VETUSDT      0.007410  2018-11-19 02:00:00  1.349528e+05   
1603    ETCUSDT      7.253200  2018-11-19 02:00:00  1.378702e+02   
762     ADAUSDT      0.057960  2018-11-19 06:00:00  1.725328e+04   
601     LTCUSDT     38.810000  2018-11-19 09:00:00  2.576656e+01   
1749    VETUSDT      0.005240  2018-11-23 00:00:00  1.908397e+05   
1430    TRXUSDT      0.013810  2018-11-23 00:00:00  7.241130e+04   
761     ADAUSDT      0.044070  2018-11-23 00:00:00  2.269117e+04   
406     BNBUSDT      5.770000  2018-11-23 00:00:00  1.733102e+02   
925     XRPUSDT      0.428310  2018-11-23 00:00:00  2.334758e+03   
292     ETHUSDT    126.630000  2018-11-23 00:00:00  7.897023e+00   
126     BTCUSDT   4370.000000  2018-11-23 00:00:00  2.288330e-01   
1290    XLMUSDT      0.187150  2018-11-23 00:00:00  5.343308e+03   
1748    VETUSDT      0.005050  2018-11-24 20:00:00  1.980198e+05   
1602    ETCUSDT      5.034500  2018-11-24 20:00:00  1.986295e+02   
600     LTCUSDT     31.430000  2018-11-24 20:00:00  3.181674e+01   
1135    EOSUSDT      3.494300  2018-11-24 20:00:00  2.861804e+02   
924     XRPUSDT      0.387380  2018-11-24 22:00:00  2.581445e+03   
291     ETHUSDT    116.460000  2018-11-24 22:00:00  8.586639e+00   
599     LTCUSDT     32.090000  2018-11-30 11:00:00  3.116236e+01 

In [29]:
with pd.option_context('display.max_rows', None):
    display(df[pd.isna(df['sell_price'])].sort_values('buy_datetime'))

Empty DataFrame
Columns: [ticker, buy_price, buy_datetime, quantity, sell_price, sell_datetime, days_to_gain_loss, price_diff, proft_loss]
Index: []

In [30]:
info = client.get_symbol_info('FLMUSDT')
print(info['filters'])

[{'filterType': 'PRICE_FILTER', 'minPrice': '0.00010000', 'maxPrice': '1000.00000000', 'tickSize': '0.00010000'}, {'filterType': 'PERCENT_PRICE', 'multiplierUp': '5', 'multiplierDown': '0.2', 'avgPriceMins': 5}, {'filterType': 'LOT_SIZE', 'minQty': '1.00000000', 'maxQty': '900000.00000000', 'stepSize': '1.00000000'}, {'filterType': 'MIN_NOTIONAL', 'minNotional': '10.00000000', 'applyToMarket': True, 'avgPriceMins': 5}, {'filterType': 'ICEBERG_PARTS', 'limit': 10}, {'filterType': 'MARKET_LOT_SIZE', 'minQty': '0.00000000', 'maxQty': '1226818.09854267', 'stepSize': '0.00000000'}, {'filterType': 'TRAILING_DELTA', 'minTrailingAboveDelta': 10, 'maxTrailingAboveDelta': 2000, 'minTrailingBelowDelta': 10, 'maxTrailingBelowDelta': 2000}, {'filterType': 'MAX_NUM_ORDERS', 'maxNumOrders': 200}, {'filterType': 'MAX_NUM_ALGO_ORDERS', 'maxNumAlgoOrders': 5}]


In [31]:
print(info['filters'][0]['tickSize'])

0.00010000


In [32]:
symbol_info = {}
def get_symbol_info(symbols):
    global symbol_info
    for symbol in symbols:
        info = client.get_symbol_info(symbol)
        base_asset = info['baseAsset']
#  PRICE_FILTER
        price_filter_min_quantity = float(info['filters'][0]['minPrice'])
        price_filter_max_quantity = float(info['filters'][0]['maxPrice'])
        price_filter_tick_size = float(info['filters'][0]['tickSize'])
        
#  LOT_SIZE (for market- and limit orders)
        lot_size_min_quantity = float(info['filters'][2]['minQty'])
        lot_size_max_quantity = float(info['filters'][2]['maxQty'])
        lot_size_step_size = float(info['filters'][2]['stepSize'])
        
#  MIN NOTIONAL
        min_notional = float(info['filters'][3]['minNotional'])
        symbol_info[symbol] = {'price_filter_min_quantity': price_filter_min_quantity, 'price_filter_max_quantity': price_filter_max_quantity,\
                               'price_filter_tick_size': price_filter_tick_size,'lot_size_min_quantity': lot_size_min_quantity, \
                                'lot_size_min_quantity': lot_size_min_quantity, 'lot_size_max_quantity': lot_size_max_quantity, \
                               'lot_size_step_size': lot_size_step_size, 'min_notional': min_notional, }
        


In [33]:
info = client.get_margin_asset(asset='BNB')

In [34]:
info

{'assetName': 'BNB',
 'assetFullName': 'Binance Coin',
 'isBorrowable': True,
 'isMortgageable': True,
 'userMinBorrow': '0',
 'userMinRepay': '0'}

In [35]:
info = client.get_margin_symbol(symbol='BURGERUSDT')

In [36]:
pair_details = client.get_all_isolated_margin_symbols()

In [37]:
info = client.get_isolated_margin_symbol(symbol='BURGERUSDT')

In [38]:
info = client.get_all_isolated_margin_symbols()

In [39]:
info = client.get_margin_price_index(symbol='MOVRUSDT')

In [40]:
info

{'symbol': 'MOVRUSDT', 'price': '17.01391739', 'calcTime': 1660335232000}

In [41]:
#transaction = client.transfer_spot_to_margin(asset='USDT', amount='100')

In [42]:
#transaction = client.create_margin_loan(asset='USDT', amount='200')

In [43]:
#transaction

In [44]:
#details = client.get_margin_loan_details(asset='USDT', txId='114199991053')

In [45]:
#transaction = client.repay_margin_loan(asset='USDT', amount='200')

In [46]:
#transaction

In [47]:
#details = client.get_margin_loan_details(asset='USDT', txId='114199991053')

In [48]:
#details

In [49]:
#order = client.create_margin_order(symbol='MOVRUSDT', side=SIDE_SELL, type='MARKET', quoteOrderQty=200, isIsolated='TRUE')

In [50]:
#transaction = client.transfer_spot_to_isolated_margin(asset='USDT', symbol='MOVRUSDT', amount='100')

In [51]:
#transaction

In [52]:
#transaction = client.create_margin_loan(asset='USDT', amount='200', symbol='MOVRUSDT', isIsolated='TRUE')

In [53]:
#transaction = client.repay_margin_loan(asset='USDT', amount='200', symbol='MOVRUSDT', isIsolated='TRUE')

In [54]:
#transaction = client.create_margin_loan(asset='MOVR', amount='200', symbol='MOVRUSDT', isIsolated='TRUE')

In [55]:
#transaction = client.transfer_isolated_margin_to_spot(asset='USDT', symbol='MOVRUSDT', amount='99.99833334')

In [56]:
#details = client.get_max_margin_transfer

In [57]:
#details

In [58]:
orders = client.get_all_margin_orders(symbol='BURGERUSDT', limit=10)

In [59]:
orders

[]

In [60]:
info = client.get_margin_account()

In [61]:
info

{'tradeEnabled': True,
 'transferEnabled': True,
 'borrowEnabled': True,
 'marginLevel': '999',
 'totalAssetOfBtc': '0.00415326',
 'totalLiabilityOfBtc': '0.00000007',
 'totalNetAssetOfBtc': '0.00415319',
 'userAssets': [{'asset': 'AGLD',
   'free': '0',
   'locked': '0',
   'borrowed': '0',
   'interest': '0',
   'netAsset': '0'},
  {'asset': 'MATIC',
   'free': '0',
   'locked': '0',
   'borrowed': '0',
   'interest': '0',
   'netAsset': '0'},
  {'asset': 'BURGER',
   'free': '0',
   'locked': '0',
   'borrowed': '0',
   'interest': '0',
   'netAsset': '0'},
  {'asset': 'STPT',
   'free': '0',
   'locked': '0',
   'borrowed': '0',
   'interest': '0',
   'netAsset': '0'},
  {'asset': 'CTXC',
   'free': '0',
   'locked': '0',
   'borrowed': '0',
   'interest': '0',
   'netAsset': '0'},
  {'asset': 'IOTX',
   'free': '0',
   'locked': '0',
   'borrowed': '0',
   'interest': '0',
   'netAsset': '0'},
  {'asset': 'TVK',
   'free': '0',
   'locked': '0',
   'borrowed': '0',
   'interest': 

In [62]:
#transaction = client.transfer_margin_to_spot(asset='BTC', amount='0.00430996')

In [63]:
transaction

NameError: name 'transaction' is not defined